# Explore `projected_shape_meters`

* Now that `map_partitions` gets us `shape_meters` in 5 min, let's use it as much as we can
* Spot check that if `loop_or_inlining==0`, we can just use this and go on
* `loop_or_inlining==1` can pose challenges, so figure out a way to bring in direction (either through normalized x, y direction vector) or readable direction
* Loop or inlining segments have proven hard to cut successfully overall, and the last bit may never be fixed. If we can use direction, it may be a bit more robust.
* Speed can be calculated either within a segment or using endpoints, and we should opt for a simpler, streamlined approach that's performant. 
* For normal shapes, we might be able to fill in the RT `stop_times` table while we're at it.

In [1]:
import altair as alt
import dask.dataframe as dd
import geopandas as gpd
import numpy as np
import pandas as pd

from segment_speed_utils import helpers
from segment_speed_utils.project_vars import SEGMENT_GCS, PROJECT_CRS
from shared_utils import rt_dates

analysis_date = rt_dates.DATES["sep2023"]

In [2]:
# Get RT trips
rt_trips = pd.read_parquet(
    f"{SEGMENT_GCS}vp_usable_{analysis_date}",
    columns = ["trip_instance_key"]
).drop_duplicates()

# Find the shape_array_key for RT trips
trip_to_shape = helpers.import_scheduled_trips(
    analysis_date,
    columns = ["trip_instance_key", "shape_array_key"],
    get_pandas = True
).merge(
    rt_trips,
    on = "trip_instance_key",
    how = "inner"
)

# Find whether it's loop or inlining
shapes_loop_inlining = pd.read_parquet(
    f"{SEGMENT_GCS}stop_segments_{analysis_date}.parquet",
    columns = ["shape_array_key", "loop_or_inlining"]
).drop_duplicates().merge(
    trip_to_shape,
    on = "shape_array_key",
    how = "inner"
)

In [3]:
ok_trips = (shapes_loop_inlining[
    shapes_loop_inlining.loop_or_inlining==0]
            .sample(25).trip_instance_key.tolist()
           )

ok_trips

['28b19dfb38fe5c5da46de2cc3e3df247',
 '201dd33c805cc1d7e391f89ac7a8872b',
 '4bbe9fe936fb76623f2d79dc0616401c',
 'bf65c2d2edfeedd63a0845efd83c1a6f',
 '689a8d183d204f9cae431e329ae76021',
 '836f2d5833687c87a6fbd0f43d38ac14',
 'df54cef699612a69a5e42bbf3d44e527',
 'eee29760668c13883032070acf37d378',
 '2a7e9fcdbd47518a9daaec8ef47db782',
 '64b91941786109c0b2fe269d1cb92467',
 'aadf5cd49c82a1f9296b0f550d51ceaf',
 '6760062875ba77b85c2f6ca433ef55cf',
 'd1d802683d6e1e51b3c3cd26c40514f6',
 '1c05bc03ecf7f72ee241122d3a8ee67d',
 'f033f42fb1be0c0eaba23b7d0ad932e0',
 '304a855735b20ef67421dbc8871fce1f',
 '5e958f629bddd3f17b56e97e26485f38',
 '0ee9ebd4c2df8b47cb5da8e4a4f07552',
 '58fedc4d0571918c9bbe52fdf5c80f66',
 '732ee78ff772f2accca488bf6b063cfd',
 '05672091920543f401b326dbfa02eb7b',
 'a04a0de53698453f34ca811eddb07dc0',
 '6fae9c44a3f889f2833c6a409bbe42cb',
 '333c25d1b413e38894a3f4648c402cfc',
 '06c5c27059367b96abd889ce4790e80e']

In [4]:
loopy_trips = (shapes_loop_inlining[
    shapes_loop_inlining.loop_or_inlining==1]
            .sample(25).trip_instance_key.tolist()
           )

loopy_trips

['6a36010c43c0bc18af09b24917f9e342',
 '4cd9d6881711ce0d12491388fd293b9d',
 '5d28104fd3e19881975c678f93ff5cf3',
 'c049d1d990dc4ca291b49bc919e0e766',
 '6fb88ff99a7ee45d266b928c3171c866',
 '360481e765279fdcfaefc3406f66a66e',
 '3567b5e468930111d7e0038019d1f041',
 'ec95ded2183b5666d9a2a3a7c25245b4',
 '2f9018dd479ce68c0af336ed4decb684',
 'e9e801a99109f8e488bc25b30d133150',
 '5bbd5bcdceb231131dfb59a8a86d5b1e',
 '039e65e6118d2072bb8d870ab4fc82ab',
 '7032664c47c5ef23ecdea4c328a30aa0',
 'cbdd7c0b7c61e0c1b9b771e93705ce17',
 '0903ae680ec963a8d49eaf3f28656b08',
 '26299729734c1a6a5bafcfb15434f5af',
 '7468466b3a6a7ff2526ac2dfb183db3d',
 '6ade9a3c7dee6d0879fbd7c14e0cf54b',
 '065cab061d1871223f5ed04aa5c22954',
 'b43e7a7fa28e1e94ad78c4bf57d7111d',
 '7ea833016442a700483a52c84b14371c',
 'dafa8a969593d3fd129421876cd92565',
 '73ebaa2e7af91fb86573e69c64b56715',
 '81ea751941112f1a783dd17ee43f26fb',
 '6449b61cde981f8e8c0e44445c438047']

In [5]:
subset_trips = ok_trips + loopy_trips

projected_shape_meters = pd.read_parquet(
    f"{SEGMENT_GCS}projection/vp_projected_{analysis_date}.parquet"
)

vp = pd.read_parquet(
    f"{SEGMENT_GCS}vp_usable_{analysis_date}",
    filters = [[("trip_instance_key", "in", subset_trips)]]
).merge(
    projected_shape_meters,
    on = "vp_idx",
    how = "inner"
).drop(columns = "location_timestamp")

In [6]:
def plot_shape_meters(df: pd.DataFrame, one_trip: str):
    """
    Plot how the projected shape meters looks for one trip.
    
    vp_idx is ordered by timestamp, use as x.
    """
    subset_df = df[df.trip_instance_key==one_trip]
    
    print(f"{subset_df.gtfs_dataset_name.iloc[0]}")
    print(f"trip_instance_key: {one_trip}, trip_id: {subset_df.trip_id.iloc[0]}")
    
    chart = (alt.Chart(subset_df)
             .mark_line()
             .encode(
                 x="vp_idx",
                 y="shape_meters:Q"
             )
            )
       
    display(chart)


In [7]:
for t in ok_trips:
    plot_shape_meters(vp, t)

Victor Valley Vehicle Position
trip_instance_key: 28b19dfb38fe5c5da46de2cc3e3df247, trip_id: 01010


alt.Chart(...)

Bay Area 511 AC Transit Vehicle Position
trip_instance_key: 201dd33c805cc1d7e391f89ac7a8872b, trip_id: 13478020


alt.Chart(...)

San Diego Vehicle Positions
trip_instance_key: 4bbe9fe936fb76623f2d79dc0616401c, trip_id: 17285181


...

alt.Chart(...)

Bay Area 511 AC Transit Vehicle Position
trip_instance_key: 333c25d1b413e38894a3f4648c402cfc, trip_id: 12125020


alt.Chart(...)

San Diego Vehicle Positions
trip_instance_key: 06c5c27059367b96abd889ce4790e80e, trip_id: 17285457


alt.Chart(...)

In [8]:
for t in loopy_trips:
    plot_shape_meters(vp, t)

GET VehiclePositions
trip_instance_key: 6a36010c43c0bc18af09b24917f9e342, trip_id: 3663


alt.Chart(...)

VCTC Vehicle Positions
trip_instance_key: 4cd9d6881711ce0d12491388fd293b9d, trip_id: 139-395


alt.Chart(...)

Bay Area 511 SamTrans VehiclePositions
trip_instance_key: 5d28104fd3e19881975c678f93ff5cf3, trip_id: 12260437-143-Blocks-Weekday-51


...

alt.Chart(...)

San Diego Vehicle Positions
trip_instance_key: 81ea751941112f1a783dd17ee43f26fb, trip_id: 17285554


alt.Chart(...)

Commerce VehiclePositions
trip_instance_key: 6449b61cde981f8e8c0e44445c438047, trip_id: 205-5


alt.Chart(...)